# Capstone 2 - Predicting Water Pump Condition in Tanzania Model

Kenneth Liao

---

## Background

The UN publishes and reviews a list of least developed countries (LDC) every 3 years. LDCs are “low-income countries confronting severe structural impediments to sustainable development. They are highly vulnerable to economic and environmental shocks and have low levels of human assets.”$^{1}$. Tanzania has been classified as an LDC since the UN published the first list of LDCs in 1971$^{2}$. A common challenge of LDCs is a lack of infrastructure to support the development of the nation, including access to education and healthcare, waste management, and potable water.

According to UNICEF, as of 2017, more than 24 million Tanzanians lacked access to basic drinking water$^{3}$. This corresponds to only 56.7% of the country’s population having access to basic drinking water. Outside of developed urban areas, much of the potable water is accessed via water pumps. 

Taarifa is an open-source platform for crowd-sourced reporting and triaging of infrastructure related issues. Together with the Tanzanian Ministry of Water, data has been collected for thousands of water pumps throughout Tanzania. The goal of this project is to be able to predict the condition of these water pumps to improve maintenance, reduce pump downtime, and ensure basic water access for tens of millions of Tanzanians.

**References**

1. https://www.un.org/development/desa/dpad/least-developed-country-category.html
2. https://www.un.org/development/desa/dpad/wp-content/uploads/sites/45/publication/ldc_list.pdf
3. https://washwatch.org/en/countries/tanzania/summary/statistics/


### Problem Description

Predict the operating condition of water pumps in Tanzania given various metadata on each water pump.

### Strategy

The strategy will be to implement a Random Forest model for multiclass classification of the state of water pumps.

### Data

The dataset is provided by Taarifa, together with the Tanzanian Ministry of Water and is hosted by DrivenData.org:

https://www.drivendata.org/competitions/7/pump-it-up-data-mining-the-water-table/page/23/

---

We first import the necessary libraries and the cleaned datasets.

In [1]:
import scipy
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from plotly.offline import iplot, plot, init_notebook_mode
from config import credentials
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, StratifiedKFold, RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import make_scorer, confusion_matrix, f1_score, recall_score, accuracy_score, precision_score
from sklearn.tree import export_graphviz
from IPython.display import Image
from subprocess import call
import joblib
from bayes_opt import BayesianOptimization
import plotly.express as px

init_notebook_mode(connected=True)

In [2]:
# load datasets
y_train = pd.read_pickle('../data/y_train.pkl')
y_test = pd.read_pickle('../data/y_test.pkl')

# save column names
feature_names = joblib.load('../data/feature_names.pkl')

# load sparse versions of X_train & X_test
X_train_s = scipy.sparse.load_npz('../data/X_train_s.npz')
X_test_s = scipy.sparse.load_npz('../data/X_test_s.npz')
X_train_s_scaled = scipy.sparse.load_npz('../data/X_train_s_scaled.npz')
X_test_s_scaled = scipy.sparse.load_npz('../data/X_test_s_scaled.npz')

In [3]:
# create class label mapping
labels = {0: 'functional', 1: 'functional needs repair', 2: 'non functional'}
labels_list = list(labels.values())

In [4]:
class_counts = dict(y_train.value_counts())
class_counts

{0: 21540, 2: 15366, 1: 2892}

## Measuring Success

In classification models it's typical to plot the receiver operating characteristic (ROC) curves and compute the area under the curve (AUC) to compare the efficacy of various models. This requires computing the sensitivity and specificity of the model which are defined below. Note that specificity is also known as recall.

<br>

\begin{equation*}
Sensitivity | Recall = \frac{True Positive}{(True Positive + False Negative)}
\end{equation*}

<br>

\begin{equation*}
Specificity = \frac{True Negative}{(True Negative + False Positive)}
\end{equation*}

<br>

These are not good metrics for classfication problems with imbalanced data. For example, if the true class comprises 99% of the data with only 1% being false, then simply guessing true for all of the data would give you 0.99 Sensitivity and 0 specificity, making your model look extremely good. However, this could be a big issue if getting that 1% correct is critical, such as in the case of classifying cancer.

For imbalanced data it's therefore more appropriate to compute the precision and recall curves which focus on the true class.

<br>


\begin{equation*}
Precision = \frac{True Positive}{(True Positive + False Positive)}
\end{equation*}

<br>

\begin{equation*}
F1 = \frac{2 * (Precision * Recall)}{(Precision + Recall)}
\end{equation*}

<br>

We're interested in predicting which pumps are functioning normally, which pumps are functioning but need to be repaired, and which pumps are completely non functioning. If a pump is non functional, it requires immediate attention as the population dependent on that water source cannot access clean water. Therefore, it's most critical that we predict this class with high recall. That is, for non functional pumps, we want to minimize the number of pumps we classify as being functional when they are actually non functional (false negatives). Of course if we took this to the extreme and assumed all pumps are non functional, we would have perfect recall but very low precision. This would be impractical because we would have to essentially send surveyors to every pump anyway to check their status, in which case the model is useless. With this in mind, the next step is to try to optimize this model to improve the recall of the non functional group without lowing too much precision.

### Helper Functions

In [5]:
def score(y_test, y_pred):
    """
    Compute precision, recall, f1 score, and classification rate.
    Classification rate is simply the accuracy of the model over
    all classes.
    """
    classification_rate = sum(y_test==y_pred)/len(y_test)
    
    scores = pd.DataFrame({'precision': precision_score(y_test, y_pred, average=None),
                           'recall': recall_score(y_test, y_pred, average=None),
                           'f1-score': f1_score(y_test, y_pred, average=None), 
                           'classification_rate': classification_rate},
            index=labels_list).T
    
    return scores

In [6]:
def random_search(X_train, y_train, X_test, clf, grid, refit_score='f1_score'):
    """
    Convenience function for RandomizedSearchCV. The
    model is refit according to the best score defined
    in the argument refit_score.
    """
    
    # split the data into stratified splits
    # for n_splits cross-validation.
    skf = StratifiedKFold(n_splits=5, random_state=42)
    
    # compute the total number of parameter combinations
    grid_size = 0
    for i in grid.values():
        grid_size+=len(i)
    
    # define the randomized search
    rs = RandomizedSearchCV(clf, grid, scoring=scorers, refit='f1_score',
                           cv=skf, return_train_score=True, n_jobs=12, 
                            random_state=42, n_iter=int(np.sqrt(grid_size)))
    
    # fit the training data
    rs.fit(X_train, y_train.values)
    
    # make predictions on the test data
    y_pred = rs.predict(X_test)
    
    # print the best model's parameters
    print(rs.best_params_)

    return rs

In [7]:
# scoring objects to pass to randomized search
scorers = {
    'precision_score': make_scorer(precision_score, average='weighted'),
    'recall_score': make_scorer(recall_score, average='weighted'),
    'f1_score': make_scorer(f1_score, average='weighted')
}

### Logistic Regression Model

I'm first going to build a baseline model using logistic regression to compare the performance of the Random Forest model to. Logistic regression models are very common and easy to implement for classification tasks. We will then see how much better we can do with Random Forest.

In [ ]:
# define the parameter grid to search
pbounds = {'C':(0.000001,10)}

In [ ]:
def logistic_regression_loss(C):
    # define logistic regression classifier
    clf = LogisticRegression(multi_class='multinomial', class_weight='balanced', 
                         penalty='l2', solver='lbfgs', C=C, random_state=42, n_jobs=-1)
    
    average_score = np.mean(cross_val_score(clf, X_train_s_scaled, y_train, cv=3, 
                                            scoring='f1_weighted', n_jobs=10))
    
    return average_score

In [ ]:
optimizer = BayesianOptimization(f=logistic_regression_loss,
                                pbounds=pbounds,
                                random_state=42)

In [ ]:
%%time
optimizer.maximize(
    init_points=5,
    n_iter=10,
)

In [ ]:
clf = LogisticRegression(multi_class='multinomial', class_weight='balanced', 
                         penalty='l2', solver='lbfgs', C=2.134, random_state=42, n_jobs=-1)

clf.fit(X_train_s_scaled, y_train)

y_pred = clf.predict(X_test_s_scaled)

score(y_test, y_pred)

### Out-of-box Random Forest

I'll start by building a baseline for which we can compare our model's results to. Recall that the majority class was **functional** which comprised 54.3% of the data. Let's see what the precision, recall, and f1-score metrics would look like for an out-of-box random forest model.

In [ ]:
%%time
# define and train the model
model = RandomForestClassifier(n_jobs=-1, random_state=42)
model.fit(X_train_s, y_train)

In [ ]:
# get the predicted labels from the model
y_pred = model.predict(X_test_s)

Let's look at the confusion matrix for the model.

In [ ]:
cols = pd.MultiIndex.from_tuples(('Actual', i) for i in labels_list)
rows = pd.MultiIndex.from_tuples(('Predicted', i) for i in labels_list)
cm = pd.DataFrame(confusion_matrix(y_test, y_pred), index=rows, columns=cols)
cm

From this summary it's easy to see that the majority of functional pumps were correctly classified as being functional. We were less accurate in correctly classifying the non functional pumps and even worse at correctly classifying the functional pumps needing repair. Let's explore this more by computing the precision, recall, and f1 scores for this data.

In [ ]:
score(y_test, y_pred)

The f1_score is highest for the functional class, followed by the non functional class. The recall for the non functional class is 0.745. This means that out of all of our predictions for non functional pumps, we were correct 74.5% the time. This is really not a bad start!

### Optimized Random Forest

The dictionary below contains the scoring functions we want to pass to the model.

In [ ]:
def random_forest_loss(max_depth, min_samples_leaf, max_features, n_estimators):
    
    #convert floats to ints
    max_depth = int(max_depth)
    min_samples_leaf = int(min_samples_leaf)
    n_estimators = int(n_estimators)
    
    # define random forest classifier
    clf = RandomForestClassifier(class_weight='balanced', max_depth=max_depth,
                                 min_samples_leaf=min_samples_leaf, 
                                 max_features=max_features, n_estimators=n_estimators,
                                 random_state=42, n_jobs=10)
    
    average_score = np.mean(cross_val_score(clf, X_train_s, y_train, cv=3, 
                                            scoring='f1_weighted', n_jobs=4))
    
    return average_score

In [ ]:
pbounds = {'max_depth': (2,100),
           'min_samples_leaf': (1,10),
           'max_features': (0.01,0.9),
           'n_estimators': (10,1000)}

In [ ]:
optimizer = BayesianOptimization(f=random_forest_loss,
                                pbounds=pbounds,
                                random_state=42)

In [ ]:
%%time
optimizer.maximize(
    init_points=5,
    n_iter=5,
)

In [ ]:
{k: 1/v for k,v in class_counts.items()}

In [ ]:
inverse_freq_weights = {k: 1/v for k,v in class_counts.items()}
bias_non_functional = {0: 4e-05, 2: 6.508e-04, 1: 0.0004}
bias_non_functional2 = {0: 1e-05, 2: 6.508e-04, 1: 0.0005}

random_grid = {'max_depth':range(2,50),
               'n_estimators': range(50,150),
               'min_samples_leaf': range(1,10),
               'max_features': ['auto', 'log2', 0.1, 0.2],
               'class_weight': ['balanced', inverse_freq_weights, 
                                bias_non_functional, bias_non_functional2]}

grid_size = 0
for i in random_grid.values():
    grid_size+=len(i)

def random_search(clf, refit_score='f1_score'):
    
    skf = StratifiedKFold(n_splits=5, random_state=42)
    
    rs = RandomizedSearchCV(clf, random_grid, scoring=scorers, refit='f1_score',
                           cv=skf, return_train_score=True, n_jobs=12, 
                            random_state=42, n_iter=int(grid_size/2))
    
    rs.fit(X_train_s, y_train.values)
    
    y_pred = rs.predict(X_test_s)
    
    print(rs.best_params_)

    return rs

In [ ]:
%%time
clf = RandomForestClassifier(random_state=42, n_jobs=12)

rs = random_search(clf)

In [ ]:
score(y_test, rs.predict(X_test_s))

Save the model to a pickle object.

Load the model back.

In [8]:
random_search_model = joblib.load('random_search.pkl')

In [9]:
y_pred = random_search_model.predict(X_test_s)

In [10]:
score(y_test, y_pred)

functional  functional needs repair  non functional
precision              0.667226                 0.797619        0.884205
recall                 0.963896                 0.047018        0.478144
f1-score               0.788582                 0.088801        0.620660
classification_rate    0.712427                 0.712427        0.712427

In [13]:
feat_importances = pd.DataFrame({'feature': feature_names, 'importance': random_search_model.best_estimator_.feature_importances_}).sort_values('importance', ascending=False).reset_index(drop=True)
feat_importances.head(10)

feature  importance
0         quantity_dry    0.059877
1            longitude    0.054795
2             latitude    0.050642
3           gps_height    0.029240
4  years_since_install    0.025220
5    construction_year    0.023259
6         day_recorded    0.022262
7           population    0.021248
8      quantity_enough    0.015268
9           amount_tsh    0.013563

In [6]:
X_train = pd.read_pickle('../data/X_train.pkl')

In [ ]:
X_train.index

In [7]:
status_map = pd.concat([X_train[['latitude','longitude']], y_train.map(labels)], axis=1)
status_map.head()

latitude  longitude    status_group
id                                        
60371 -3.025106  31.767301  non functional
17088 -6.030500  36.322623      functional
16532 -1.692329  30.969200  non functional
11098 -3.184940  37.610301      functional
20249 -4.417159  32.748950      functional

In [8]:
quantity_map = pd.concat([X_train[['latitude','longitude', 'quantity_dry']], y_train.map(labels)], axis=1)
quantity_map.head()

latitude  longitude  quantity_dry    status_group
id                                                      
60371 -3.025106  31.767301             0  non functional
17088 -6.030500  36.322623             0      functional
16532 -1.692329  30.969200             0  non functional
11098 -3.184940  37.610301             0      functional
20249 -4.417159  32.748950             0      functional

In [21]:
distances = X_train[['latitude','longitude']]

In [25]:
distances.loc[:,'lat_radians'] = np.radians(distances.latitude)
distances.loc[:,'lon_radians'] = np.radians(distances.longitude)

C:\Users\Kenny\Anaconda3\lib\site-packages\pandas\core\indexing.py:576: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [26]:
earth_radius=6371

a = np.sin((lat2-lat1)/2.0)**2 + \
        np.cos(lat1) * np.cos(lat2) * np.sin((lon2-lon1)/2.0)**2

    return earth_radius * 2 * np.arcsin(np.sqrt(a))

latitude  longitude  lat_radians  lon_radians
id                                                  
60371 -3.025106  31.767301    -0.052798     0.554444
17088 -6.030500  36.322623    -0.105252     0.633949
16532 -1.692329  30.969200    -0.029537     0.540515
11098 -3.184940  37.610301    -0.055588     0.656424
20249 -4.417159  32.748950    -0.077094     0.571577
...         ...        ...          ...          ...
68525 -8.774761  36.367112    -0.153148     0.634726
11980 -9.769604  34.531524    -0.170512     0.602689
35778 -5.420823  38.974416    -0.094611     0.680232
49444 -3.107161  34.316586    -0.054230     0.598937
23812 -3.211457  37.626401    -0.056051     0.656705

[39798 rows x 4 columns]

In [12]:
np.radians([quantity_map.loc[60371,'latitude'], quantity_map.loc[60371,'longitude']])

array([-0.05279805,  0.554444  ])

In [18]:
# vectorized haversine function
def haversine(lat1, lon1, lat2, lon2, to_radians=True, earth_radius=6371):
    """
    slightly modified version: of http://stackoverflow.com/a/29546836/2901002

    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees or in radians)

    All (lat, lon) coordinates must have numeric dtypes and be of equal length.

    """
    if to_radians:
        lat1, lon1, lat2, lon2 = np.radians([lat1, lon1, lat2, lon2])

    a = np.sin((lat2-lat1)/2.0)**2 + \
        np.cos(lat1) * np.cos(lat2) * np.sin((lon2-lon1)/2.0)**2

    return earth_radius * 2 * np.arcsin(np.sqrt(a))

In [20]:
import numpy
haversine(quantity_map['longitude'].shift().values, quantity_map['latitude'].shift().values,
                 quantity_map.loc[1:, 'longitude'].values, quantity_map.loc[1:, 'latitude'].values)

AttributeError: 'numpy.ndarray' object has no attribute 'radians'

In [29]:
px.set_mapbox_access_token(credentials['mapbox_token'])

fig = px.scatter_mapbox(status_map, lat="latitude", lon="longitude", 
                        color='status_group',
                        size_max=15, zoom=4.5)
fig.show()

In [36]:
px.set_mapbox_access_token(credentials['mapbox_token'])

fig = px.scatter_mapbox(quantity_map, lat="latitude", lon="longitude", 
                        color='quantity_dry',
                        size_max=15, zoom=4.5)
fig.show()

The top 10 most important features in the random forest model are shown above. 

Take the best model and now just play with the weights to try to improve the performance on non functional and needs repair

### Hyperparameter Tuning & Model Optimization

To optimize the model, I reduced the max_depth to 5 and increased the number of estimators to 10,000 to reduce overfitting the train data. I also played with the weights given to each class to emphasize the "non functional" class. The results of the model above shows that we were able to increase the recall of the "non functional" pumps from 0.74 to 0.75 by increasing the weight of that class. This is an improvement of 1% over the baseline model. However, the precision suffered and dropped from 0.83 to 0.6! The next step would be to run an exhaustive grid search to find the optimal model to improve the recall of "non functional" pumps while maintaining the f1-score to ensure we don't lose too much precision

The model found that the gps location (latitude, longitude, and height) of water pumps is critical in determining whether they are functioning or not. One feature which I engineered "years_since_install" was also among the top 5 most important features. This is not surprising since things manufactured goods tend to degrade over time, especially with high usage and weather.

### Interpretation

In [ ]:
clf = RandomForestClassifier(random_state=42, max_depth=2, n_estimators=100, n_jobs=-1)

clf.fit(X_train_s, y_train.values)

estimator = clf.estimators_[50]

In [ ]:
estimator

In [ ]:


# Export as dot file
export_graphviz(estimator, out_file='tree.dot', 
                feature_names = X_train.columns,
                class_names = labels_list,
                rounded = True, proportion = False, 
                precision = 2, filled = True)

In [ ]:
# Convert to png using system command (requires Graphviz)

call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in jupyter notebook

Image(filename = 'tree.png')

## Conlusions

I trained a Random Forest model to classify water pumps as "functional", "function needs repair", and non functional. I focused on improving the recall score for accurately predicting "non functional" pumps, as this class is the most critical in getting right. The model is able to predict "non functional" water pumps with a precision of and a recall of . This is a great start to accurately deploying resources where they are needed the most, and to ensure that Tanzanians have access to clean, potable water.

## Next Steps

Seeing how gps latitude and longitude were the two most important features in this model. I would like to explore this more by finding correlations between those two features and the other features. Why does the location matter? Are the "non functional" pumps clumped together around certain geographical regions? Why are those areas so different? The first step to answering these questions would be to plot the locations of failing pumps and explore how the rest of the features are stratified for these broken pumps.